# Main notebook for battery state estimation

In [1]:
import numpy as np
import pandas as pd
import scipy.io
import math
import os
import ntpath
import sys
import logging
import time
import sys

from importlib import reload
import plotly.graph_objects as go

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import SGD, Adam
from keras.utils import np_utils
from keras.layers import LSTM, Embedding, RepeatVector, TimeDistributed, Masking
from keras.callbacks import EarlyStopping, ModelCheckpoint, LambdaCallback


IS_COLAB = False

if IS_COLAB:
    from google.colab import drive
    drive.mount('/content/drive')
    data_path = "/content/drive/My Drive/battery-state-estimation/battery-state-estimation/"
else:
    data_path = "../"

sys.path.append(data_path)
from data_processing.unibo_powertools_data import UniboPowertoolsData, CycleCols
from data_processing.model_data_handler import ModelDataHandler

Using TensorFlow backend.


### Config logging

In [2]:
reload(logging)
logging.basicConfig(format='%(asctime)s [%(levelname)s]: %(message)s', level=logging.DEBUG, datefmt='%Y/%m/%d %H:%M:%S')

# Load Data

### Initial the data object

Load the cycle and capacity data to memory based on the specified chunk size

In [3]:
dataset = UniboPowertoolsData(
    test_types=['S'],
    chunk_size=1000000,
    lines=[37, 40],
    charge_line=37,
    discharge_line=40,
    base_path=data_path
)

2020/12/02 16:23:32 [DEBUG]: Start loading data with lines: [37, 40], types: ['S'] and chunksize: 1000000...
2020/12/02 16:24:00 [DEBUG]: Finish loading data.
2020/12/02 16:24:00 [INFO]: Loaded raw dataset A data with cycle row count: 6181604 and capacity row count: 16548
2020/12/02 16:24:00 [DEBUG]: Start cleaning cycle raw data...
2020/12/02 16:24:05 [DEBUG]: Finish cleaning cycle raw data.
2020/12/02 16:24:05 [INFO]: Removed 5 rows of abnormal cycle raw data.
2020/12/02 16:24:05 [DEBUG]: Start cleaning capacity raw data...
2020/12/02 16:24:05 [DEBUG]: Finish cleaning capacity raw data.
2020/12/02 16:24:05 [INFO]: Removed 1 rows of abnormal capacity raw data.
2020/12/02 16:24:05 [DEBUG]: Start assigning charging raw data...
2020/12/02 16:24:06 [DEBUG]: Finish assigning charging raw data.
2020/12/02 16:24:06 [INFO]: [Charging] cycle raw count: 4773746, capacity raw count: 8278
2020/12/02 16:24:06 [DEBUG]: Start assigning discharging raw data...
2020/12/02 16:24:06 [DEBUG]: Finish assi

### Determine the training and testing name

Prepare the training and testing data for model data handler to load the model input and output data.

In [4]:
train_data_test_names = [
    '000-DM-3.0-4019-S', 
    '001-DM-3.0-4019-S', 
    '002-DM-3.0-4019-S', 
    '006-EE-2.85-0820-S', 
    '007-EE-2.85-0820-S', 
    '018-DP-2.00-1320-S', 
    '019-DP-2.00-1320-S',
    '036-DP-2.00-1720-S', 
    '037-DP-2.00-1720-S', 
    '038-DP-2.00-2420-S', 
    '040-DM-4.00-2320-S',
    '042-EE-2.85-0820-S', 
    '045-BE-2.75-2019-S'
]

test_data_test_names = [
    '003-DM-3.0-4019-S',
    '008-EE-2.85-0820-S',
    '039-DP-2.00-2420-S', 
    '041-DM-4.00-2320-S',    
]

dataset.prepare_data(train_data_test_names, test_data_test_names)

2020/12/02 16:24:06 [DEBUG]: Start preparing data for training: ['000-DM-3.0-4019-S', '001-DM-3.0-4019-S', '002-DM-3.0-4019-S', '006-EE-2.85-0820-S', '007-EE-2.85-0820-S', '018-DP-2.00-1320-S', '019-DP-2.00-1320-S', '036-DP-2.00-1720-S', '037-DP-2.00-1720-S', '038-DP-2.00-2420-S', '040-DM-4.00-2320-S', '042-EE-2.85-0820-S', '045-BE-2.75-2019-S'] and testing: ['003-DM-3.0-4019-S', '008-EE-2.85-0820-S', '039-DP-2.00-2420-S', '041-DM-4.00-2320-S']...
2020/12/02 16:24:17 [DEBUG]: Finish getting training and testing charge data.
2020/12/02 16:24:24 [DEBUG]: Finish getting training and testing discharge data.
2020/12/02 16:24:24 [DEBUG]: Finish cleaning training and testing charge data.
2020/12/02 16:24:24 [DEBUG]: Finish cleaning training and testing discharge data.
2020/12/02 16:24:25 [DEBUG]: Finish adding training and testing discharge SOC parameters.
2020/12/02 16:24:29 [DEBUG]: Finish adding training and testing discharge SOH parameters.
2020/12/02 16:24:29 [DEBUG]: Finish preparing da

### Initial the model data handler

Model data handler will be used to get the model input and output data for further training purpose.

In [5]:
mdh = ModelDataHandler(dataset, [
    CycleCols.VOLTAGE,
    CycleCols.CURRENT,
    CycleCols.TEMPERATURE
])

# Data loading

In [6]:
train_x, train_y, test_x, test_y = mdh.get_discharge_whole_cycle(soh = False, output_capacity = True)

2020/12/02 16:24:35 [INFO]: Train x: (6536, 287, 3), train y: (6536, 287, 2) | Test x: (1728, 287, 3), test y: (1728, 287, 2)


In [7]:
train_y = mdh.keep_only_capacity(train_y, is_multiple_output = True)
test_y = mdh.keep_only_capacity(test_y, is_multiple_output = True)

2020/12/02 16:24:35 [INFO]: New y: (6536, 287)
2020/12/02 16:24:35 [INFO]: New y: (1728, 287)


In [8]:
# Model definition

#opt = tf.keras.optimizers.Adam(lr=0.00001)

#model = Sequential()
#model.add(LSTM(256, activation='selu',
#                return_sequences=True,
#                input_shape=(train_x.shape[1], train_x.shape[2])))
#model.add(LSTM(256, activation='selu', return_sequences=True))
#model.add(LSTM(128, activation='selu', return_sequences=True))
#model.add(Dense(64, activation='selu'))
#model.add(Dense(1, activation='linear'))
#model.summary()

#model.compile(optimizer=opt, loss='huber', metrics=['mse', 'mae', 'mape', tf.keras.metrics.RootMeanSquaredError(name='rmse')])

In [9]:
experiment_name = '2020-12-02-12-28-17_lstm_soc'

history = pd.read_csv(data_path + 'results/trained_model/%s_history.csv' % experiment_name)
model = keras.models.load_model(data_path + 'results/trained_model/%s.h5' % experiment_name)
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm (LSTM)                  (None, 287, 256)          266240    
_________________________________________________________________
lstm_1 (LSTM)                (None, 287, 256)          525312    
_________________________________________________________________
lstm_2 (LSTM)                (None, 287, 128)          197120    
_________________________________________________________________
dense (Dense)                (None, 287, 64)           8256      
_________________________________________________________________
dense_1 (Dense)              (None, 287, 1)            65        
Total params: 996,993
Trainable params: 996,993
Non-trainable params: 0
_________________________________________________________________


In [10]:
print(history)

    Unnamed: 0      loss       mse       mae        mape      rmse  val_loss  \
0            0  0.061454  0.130926  0.176827  68217104.0  0.361837  0.057110   
1            1  0.024609  0.052666  0.082979  39745644.0  0.229491  0.042217   
2            2  0.016489  0.035012  0.065923  28633566.0  0.187116  0.044952   
3            3  0.013216  0.028064  0.056761  22587940.0  0.167523  0.046660   
4            4  0.011179  0.023606  0.049706  19316846.0  0.153643  0.045198   
5            5  0.009834  0.020695  0.044973  17313346.0  0.143856  0.041662   
6            6  0.008983  0.019031  0.041983  15911847.0  0.137951  0.044927   
7            7  0.008071  0.017097  0.037511  14347060.0  0.130756  0.044105   
8            8  0.007457  0.015863  0.035304  13124109.0  0.125946  0.038438   
9            9  0.006874  0.014615  0.033521  12020897.0  0.120893  0.040624   
10          10  0.006627  0.014172  0.033739  11628951.0  0.119046  0.047866   
11          11  0.006136  0.013155  0.03

### Testing

In [11]:
results = model.evaluate(test_x, test_y)
print(results)

54/54 [==============================] - 15s 275ms/step - loss: 0.0307 - mean_squared_error: 0.0883 - mean_absolute_error: 0.0663 - mean_absolute_percentage_error: 8246502.0000 - rmse: 0.2972
[0.030748441815376282, 0.08832339197397232, 0.06625419855117798, 8246502.0, 0.2971925139427185]


# Data Visualization

In [12]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=history['loss'],
                    mode='lines', name='train'))
fig.add_trace(go.Scatter(y=history['val_loss'],
                    mode='lines', name='validation'))
fig.update_layout(title='Loss trend',
                  xaxis_title='epoch',
                  yaxis_title='loss',
                  width=1400,
                  height=600)
fig.show()

In [13]:
train_predictions = model.predict(train_x)

In [14]:
cycle_num = 0
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=train_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=train_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on training',
                  xaxis_title='Cycle',
                  yaxis_title='Capacity',
                  width=1400,
                  height=600)
fig.show()

In [15]:
cycle_num = 10
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=train_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=train_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on training',
                  xaxis_title='Cycle',
                  yaxis_title='Capacity',
                  width=1400,
                  height=600)
fig.show()

In [16]:
cycle_num = 100
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=train_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=train_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on training',
                  xaxis_title='Cycle',
                  yaxis_title='Capacity',
                  width=1400,
                  height=600)
fig.show()

In [17]:
test_predictions = model.predict(test_x)

In [18]:
cycle_num = 0
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=test_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=test_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on testing',
                  xaxis_title='Cycle',
                  yaxis_title='Capacity',
                  width=1400,
                  height=600)
fig.show()

In [19]:
cycle_num = 40
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=test_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=test_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on testing',
                  xaxis_title='Cycle',
                  yaxis_title='Capacity',
                  width=1400,
                  height=600)
fig.show()